In [2]:
import pandas as pd
import os
import gc
import json
import cv2
from tqdm.auto import tqdm
from HCFA_OCR_XML_to_DataFrame import *

In [3]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')
gc.collect()

37

In [4]:
HCFA_final_keys = pd.read_excel(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_Keys_list_verification.xlsx", sheet_name = 'Field_Names from KEY file')

In [5]:
HCFA_final_keys

Key_Name
0     10A_PatConditionEmpN
1     10A_PatConditionEmpY
2           10B_PatAAState
3    10B_PatConditionAutoN
4    10B_PatConditionAutoY
..                     ...
152          9B_SecInsSexM
153      9D_SecInsPlanName
154       31_RenDateSigned
155      11B_PriInsEmpName
156    24J_RenProvFullName

[157 rows x 1 columns]

In [6]:
key_names = HCFA_final_keys['Key_Name'].tolist()

In [7]:
def get_charges(row):
    ground_truth = row["Data"]
    return ground_truth

In [8]:
def get_Pat_details(row):
    if "?" not in str(row["OCR_Optimizer"]):
        ground_truth = row["OCR_Optimizer"]
    else:
        if row["Data"] != '[BLANK]':
            ground_truth = row["Data"]
        else:
            ground_truth = row["OCR_Optimizer"].replace("?", " ")
    if ground_truth == ' ':
        ground_truth = '[BLANK]'
    return ground_truth

In [9]:
def generate_ground_truth(row):
    ground_truth = '[BLANK]'
    try:
        if row["Field_Name"] in ['28_TotalCharges','29_AmountPaid', '30_BalanceDue']:
            ground_truth = get_charges(row)
        elif row["Field_Name"] in['5_PatAddr1', '5_PatCity', '5_PatPostCode', '5_PatState']:
            ground_truth = get_Pat_details(row)
        else:
            if "?" not in str(row["OCR_Optimizer"]):
                if row["OCR_Optimizer"] != '[BLANK]':
                    ground_truth = row["OCR_Optimizer"]
                else:
                    ground_truth = row["Data"]
    except:
        ground_truth = row["Data"]
    if "@" in ground_truth:
        ground_truth = '[BLANK]'
    return ground_truth

In [10]:
def create_annotation_dict(df):
    result_dict = {}
    for index, row in df.iterrows():
        field_name = row['Field_Name']
        gt_value = row['Data']
        if field_name in result_dict:
            if pd.notna(field_name):
                result_dict[field_name] = f"{result_dict[field_name]}; {gt_value}"    
        else:
            result_dict[field_name] = gt_value

    return result_dict

In [11]:
import os
img_files = os.listdir(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\train\img")
print(len(img_files))
print(img_files[0])

27913
BSC134A9O001_001.tiff


In [11]:
# import xml.etree.ElementTree as ET
# xml_file_path = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\train\key\BSC134A9O001_000_HCFA.KEY"
# # Parse the XML file
# tree = ET.parse(xml_file_path)
# root = tree.getroot()
# # Iterate through all <Fld> elements
# for fld in root.findall('.//Fld'):
#     typ = fld.get('Typ')  # Get the 'Typ' attribute
#     if typ == 'SINGLE':  # If Typ is 'SINGLE', follow the previous logic
#         nm_element = fld.find('.//Nm')
#         if nm_element is not None:
#             print(nm_element.text)
#     elif typ in ['GROUP', 'TABLE']:  # If Typ is 'GROUP' or 'TABLE', follow the new logic
#         clms = fld.findall('.//Clm')
#         for clm in clms:
#             nm_value = clm.get('Nm')
#             if nm_value:
#                 print(nm_value)

In [12]:
json_target_path = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\train\key"
images_source_path = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\train\img"
images_target_path = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\train\img"
Key_dir = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\train\key"

In [14]:
os.makedirs(json_target_path, exist_ok=True)
os.makedirs(images_target_path, exist_ok=True)

In [15]:
import gc
gc.collect()
import os
import json
import shutil
from tqdm import tqdm

file_counter = 0
for file in tqdm(os.listdir(Key_dir)):
    try:
        Annotation_dict = {}
        xml_file_name = os.path.join(Key_dir, file)
        grnd_df, single_fields, grp_field_names, table_field_names, image_name = OCR_XML_to_DataFrame(xml_file_name, key_names)
        
        if image_name[0][0] in img_files:
            # Generate ground truth and create annotation dictionary
            grnd_df.fillna("[BLANK]", inplace=True)
            grnd_df["Ground_truth"] = grnd_df.apply(generate_ground_truth, axis=1)
            Annotation_dict = create_annotation_dict(grnd_df)

            # Generate the base filename (without extension)
            base_filename = os.path.splitext(file)[0]

            # Save the annotation dictionary as JSON with the base filename
            json_file_path = os.path.join(json_target_path, base_filename + ".json")
            with open(json_file_path, 'w') as json_file:
                json.dump(Annotation_dict, json_file)

            source_image_path = os.path.join(images_source_path, image_name[0][0])
            target_image_path = os.path.join(images_target_path, base_filename + os.path.splitext(image_name[0][0])[1])
            if os.path.exists(source_image_path):
                shutil.copy(source_image_path, target_image_path)

#             print(f"{file} : {len(Annotation_dict)}")
#             print(Annotation_dict)
    
    except Exception as e:
        raise e

    file_counter += 1
    if file_counter%200 == 0:
        gc.collect()

100%|██████████████████████████████████████████████████████████████████████████| 27919/27919 [1:48:46<00:00,  4.28it/s]


In [40]:
import pandas as pd
import json
from tqdm import tqdm
key_file_dir = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\valid\key"
train_key_files = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\train\key"

In [50]:
import os
import json

files_with_151 = []
files_with_157 = []
others = []
key_files = os.listdir(train_key_files)
for each_key_file in tqdm(key_files):
    each_path = os.path.join(train_key_files, each_key_file)   
    # Reading the JSON file
    with open(each_path, 'r') as file:
        data = json.load(file)
        if len(data) == 151:
            files_with_151.append(each_key_file)
        elif len(data) == 157:
            files_with_157.append(each_key_file)
        else:
            others.append(each_key_file)
print(len(files_with_151), len(files_with_157), len(others))

100%|██████████████████████████████████████████████████████████████████████████| 27919/27919 [00:14<00:00, 1925.41it/s]


0 27919 0


In [33]:
others

[]

In [47]:
import os
import json
from tqdm import tqdm

extra_keys = {
    "24_AnesStartTime": "[BLANK]",
    "24_AnesEndTime": "[BLANK]",
    "24_AnesTotalTime": "[BLANK]",
    "24_AnesTotalMin": "[BLANK]",
    "24_AnesMod": "[BLANK]",
    "24_AnesUnits": "[BLANK]"
}

files_with_151 = []
files_with_157 = []
others = []
train_key_files = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\donut_data\train\key"

key_files = os.listdir(train_key_files)
for each_key_file in tqdm(key_files):
    each_path = os.path.join(train_key_files, each_key_file)   
    # Reading the JSON file
    with open(each_path, 'r') as file:
        data = json.load(file)
        
        if len(data) == 151:
            files_with_151.append(each_key_file)
            # Add the extra keys and values
            data.update(extra_keys)
            
            # Save the updated JSON data back to the file
            with open(each_path, 'w') as file:
                json.dump(data, file, indent=4)
                
        elif len(data) == 157:
            files_with_157.append(each_key_file)
        else:
            others.append(each_key_file)

print(f"Files with 151 keys: {len(files_with_151)}")
print(f"Files with 157 keys: {len(files_with_157)}")
print(f"Other files: {len(others)}")


100%|███████████████████████████████████████████████████████████████████████████| 27919/27919 [01:19<00:00, 353.14it/s]

Files with 151 keys: 27320
Files with 157 keys: 599
Other files: 0
